In [1]:
import cv2
import numpy as np

In [29]:
videofeed = 'intruder_1.mp4'
video_cap = cv2.VideoCapture(videofeed)
if not video_cap:
    print("Unable to open the source: {filename}".format(filename=videofeed))

In [22]:
img = cv2.imread('Quiz5_1.jpg', cv2.IMREAD_COLOR)
imgGray = cv2.cvtColor(img, cv2.COLOR_BGR2GRAY)

ret1, thresh1 = cv2.threshold(imgGray, 127, 255, cv2.THRESH_BINARY)
contours1, hierarchy1 = cv2.findContours( thresh1, cv2.RETR_LIST, cv2.CHAIN_APPROX_SIMPLE)

ret2, thresh2 = cv2.threshold(imgGray, 127, 255, cv2.THRESH_BINARY_INV)
contours2, hierarchy2 = cv2.findContours( thresh2, cv2.RETR_LIST, cv2.CHAIN_APPROX_SIMPLE)

print('Number of contours case 1 : ', len(contours1))
print('Number of contours case 2 : ', len(contours2))

Number of contours case 1 :  3
Number of contours case 2 :  2


In [30]:
help(cv2)

Help on package cv2.cv2 in cv2:

NAME
    cv2.cv2 - Python wrapper for OpenCV.

PACKAGE CONTENTS
    cv2
    data (package)
    version

CLASSES
    builtins.Exception(builtins.BaseException)
        cv2.error
    builtins.object
        cv2.Algorithm
            cv2.AlignExposures
                cv2.AlignMTB
            cv2.BackgroundSubtractor
                cv2.BackgroundSubtractorKNN
                cv2.BackgroundSubtractorMOG2
                cv2.bgsegm_BackgroundSubtractorCNT
                cv2.bgsegm_BackgroundSubtractorGMG
                cv2.bgsegm_BackgroundSubtractorGSOC
                cv2.bgsegm_BackgroundSubtractorLSBP
                cv2.bgsegm_BackgroundSubtractorMOG
            cv2.BaseCascadeClassifier
            cv2.CLAHE
            cv2.CalibrateCRF
                cv2.CalibrateDebevec
                cv2.CalibrateRobertson
            cv2.DenseOpticalFlow
                cv2.DISOpticalFlow
                cv2.FarnebackOpticalFlow
                cv2.Variational

In [31]:
width = int(video_cap.get(cv2.CAP_PROP_FRAME_WIDTH))
height = int(video_cap.get(cv2.CAP_PROP_FRAME_HEIGHT))
fps=20

framesize = (width,height)
size_quad = (int(2*width),int(2*height))

video_out_alert_file = 'video_out_alert_1.mp4'
video_out_quad_file = 'video_out_quad_1.mp4'

video_out_alert = cv2.VideoWriter(video_out_alert_file,cv2.VideoWriter_fourcc(*'MP4V'),fps,framesize)
video_out_quad_file = cv2.VideoWriter(video_out_quad_file,cv2.VideoWriter_fourcc(*'MP4V'),fps,size_quad)

In [32]:
def drawBannerText(frame, text, banner_height_percent = 0.08, font_scale = 0.8, text_color = (0,255,0), font_thickness = 2):
    banner_height = int(banner_height_percent * frame.shape[0])
    cv2.rectangle(frame,(0,0),(frame.shape[1],banner_height),(0,0,0), thickness=-1)
    left_offset = 20
    location = (left_offset, int(10 + (banner_height_percent * frame.shape[0])/2))
    cv2.putText(frame,text,location,cv2.FONT_HERSHEY_SIMPLEX, font_scale, text_color, font_thickness, cv2.LINE_AA)

In [33]:
bg_sub = cv2.createBackgroundSubtractorKNN(history = 200)

In [34]:
help(cv2)

Help on package cv2.cv2 in cv2:

NAME
    cv2.cv2 - Python wrapper for OpenCV.

PACKAGE CONTENTS
    cv2
    data (package)
    version

CLASSES
    builtins.Exception(builtins.BaseException)
        cv2.error
    builtins.object
        cv2.Algorithm
            cv2.AlignExposures
                cv2.AlignMTB
            cv2.BackgroundSubtractor
                cv2.BackgroundSubtractorKNN
                cv2.BackgroundSubtractorMOG2
                cv2.bgsegm_BackgroundSubtractorCNT
                cv2.bgsegm_BackgroundSubtractorGMG
                cv2.bgsegm_BackgroundSubtractorGSOC
                cv2.bgsegm_BackgroundSubtractorLSBP
                cv2.bgsegm_BackgroundSubtractorMOG
            cv2.BaseCascadeClassifier
            cv2.CLAHE
            cv2.CalibrateCRF
                cv2.CalibrateDebevec
                cv2.CalibrateRobertson
            cv2.DenseOpticalFlow
                cv2.DISOpticalFlow
                cv2.FarnebackOpticalFlow
                cv2.Variational

In [35]:
ksize = (5,5)
max_contours = 3
frame_count = 0
frame_start = 5
red = (0,0,255)
yellow = (0,255,255)
green = (0,255,0)

while True:
    ret, frame = video_cap.read()
    if(frame is None):
        break
    else:
        frame_count += 1
        frame_erode_c = frame.copy()
    fg_mask = bg_sub.apply(frame)
    if frame_count > frame_start:
        motion_area = cv2.findNonZero(fg_mask)
        if(motion_area is not None):
            x, y, w, h = cv2.boundingRect(motion_area)
            cv2.rectangle(frame,(x,y),(x+w,y+h), red, thickness = 2)
            drawBannerText(frame, 'Intrusion Alert', text_color=red)
        fg_mask_erode_c = cv2.erode(fg_mask, np.ones(ksize, np.uint8))
        motion_area_erode = cv2.findNonZero(fg_mask_erode_c)
        if motion_area_erode is not None:
            xe, ye, we, he = cv2.boundingRect(motion_area_erode)
            cv2.rectangle(frame_erode_c,(xe,ye),(xe+we,ye+he),red,thickness=2)
            drawBannerText(frame_erode_c,'Intrusion Alert', text_color=red)
        frame_fg_mask = cv2.cvtColor(fg_mask,cv2.COLOR_GRAY2BGR)
        frame_fg_mask_erode_c = cv2.cvtColor(fg_mask_erode_c, cv2.COLOR_GRAY2BGR)
        contours_erode, hierarchy = cv2.findContours(fg_mask_erode_c, cv2.RETR_LIST, cv2.CHAIN_APPROX_SIMPLE)
        if len(contours_erode) > 0:

            # Annotate eroded foreground mask with cotours.
            cv2.drawContours(frame_fg_mask_erode_c, contours_erode, -1, green, thickness=2)

            # Sort contours based on area.
            contours_sorted = sorted(contours_erode, key=cv2.contourArea, reverse=True)
            
            # Compute bounding rectangle for the top N largest contours.
            for idx in range(min(max_contours, len(contours_sorted))):
                xc, yc, wc, hc = cv2.boundingRect(contours_sorted[idx])
                if idx == 0:
                    x1 = xc
                    y1 = yc
                    x2 = xc + wc
                    y2 = yc + hc
                else:
                    x1 = min(x1, xc)
                    y1 = min(y1, yc)
                    x2 = max(x2, xc + wc)
                    y2 = max(y2, yc + hc)

            # Draw bounding rectangle for top N contours on output frame.
            cv2.rectangle(frame_erode_c, (x1, y1), (x2, y2), yellow, thickness=2)
            drawBannerText(frame_erode_c, 'Intrusion Alert', text_color=red)

        # Annotate each video frame.
        drawBannerText(frame_fg_mask, 'Foreground Mask')
        drawBannerText(frame_fg_mask_erode_c, 'Foreground Mask (Eroded + Contours)')

        # Build quad view.
        frame_top = np.hstack([frame_fg_mask, frame])
        frame_bot = np.hstack([frame_fg_mask_erode_c, frame_erode_c])
        frame_composite = np.vstack([frame_top, frame_bot])

        # Annotate quad view with dividers.
        fc_h, fc_w, _= frame_composite.shape
        cv2.line(frame_composite, (int(fc_w/2), 0), (int(fc_w/2), fc_h), yellow , thickness=3, lineType=cv2.LINE_AA)
        cv2.line(frame_composite, (0, int(fc_h/2)), (fc_w, int(fc_h/2)), yellow, thickness=3, lineType=cv2.LINE_AA)

        # Write video output files.
        video_out_alert.write(frame_erode_c)    # Alert 
        video_out_quad_file.write(frame_composite)   # Analysis quad view

video_cap.release()
video_out_alert.release()
video_out_quad_file.release()